In [12]:
from obspy.core.util.attribdict import AttribDict
from obspy.core.inventory import Inventory, read_inventory
from infrapy.detection import beamforming_new
from pathlib import Path
import pandas as pd
from obspy import read
import re
import glob
import os

def sac_file_parser(filepath):
    filename = os.path.basename(filepath)
    parts = filename.split('.')
    network = parts[0]
    station = parts[1]
    channel = parts[2]
    times = ''.join(parts[3:-1])  # Exclude the extension part
    return network, station, channel, times

def sac_path_grouping(folder_path):
    # Get a list of all .sac files in the folder
    sac_files = list(Path(folder_path).rglob('*.sac'))

    # Dictionary to hold the grouped paths
    grouped_paths = {}

    # Parse and group the file paths
    for sac_file in sac_files:
        network, station, channel, times = sac_file_parser(sac_file.name)
        key = (network, channel, times)
        grouped_path = f"{sac_file.parent}/{network}.I06H*.{channel}.{times}.sac"
        grouped_paths[key] = grouped_path

    # Create a DataFrame from the grouped paths
    df_grouped_paths = pd.DataFrame(list(grouped_paths.values()), columns=['GroupedFilePath'])
    
    return df_grouped_paths

In [16]:
folder_path = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_SAC'
df_grouped_file_paths = sac_path_grouping(folder_path)
print(df_grouped_file_paths)

                                       GroupedFilePath
0    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
1    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
2    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
3    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
4    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
..                                                 ...
431  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
432  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
433  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
434  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
435  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...

[436 rows x 1 columns]


In [21]:
import sys
sys.path.append('/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/')
from src.utils import *

sac_path_grouping('/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_SAC')

GroupedFilePath
0    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
1    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
2    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
3    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
4    /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
..                                                 ...
431  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
432  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
433  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
434  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...
435  /run/media/viblab/Markov2/Haykal/AnakKrakatauE...

[436 rows x 1 columns]

In [10]:
import os
import pandas as pd
from infrapy.utils.data_io import json_to_detection_list

def extract_det_from_csv(csv_folder, detection_file, output_folder):
    # Ensure the output folder exists
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Load the detection file
    detections = json_to_detection_list(detection_file)

    # Get a list of all CSV files in the folder
    csv_files = [f for f in os.listdir(csv_folder) if f.endswith('.csv')]

    # Process each CSV file
    for file in csv_files:
        file_path = os.path.join(csv_folder, file)

        # Read the CSV file, assuming the first column contains the timestamp
        df = pd.read_csv(file_path, index_col=0)
        df.index = pd.to_datetime(df.index)  # Convert the index to datetime

        # Iterate over each detection
        for i, det in enumerate(detections):
            # Define start and end times for slicing
            t_start = pd.to_datetime(det.peakF_UTCtime) + pd.to_timedelta(det.start, 's')
            t_end = pd.to_datetime(det.peakF_UTCtime) + pd.to_timedelta(det.end, 's')

            # Filter the DataFrame for the given detection time range
            trimmed_df = df[(df.index >= t_start) & (df.index <= t_end)]

            # Check if the trimmed DataFrame is empty
            if trimmed_df.empty:
                print(f"No data in range for {file} detection {i}, skipping...")
                continue

            # Save the trimmed DataFrame to a new CSV file in the output folder
            trimmed_filename = os.path.join(output_folder, f"{file.split('.')[0]}_det_{i}_trimmed.csv")
            trimmed_df.to_csv(trimmed_filename, index=True)
            print(f"Saved trimmed data to {trimmed_filename}")

# Example usage of the function
csv_folder = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_CSV'
detection_file = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/Trimmed_Confirmed_Events.json'
output_folder = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/processed/I06AU_DETS'
extract_det_from_csv(csv_folder, detection_file, output_folder)


No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 0, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 1, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 2, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 3, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 4, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 5, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 6, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 7, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 8, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 9, skipping...


ParserError: Error tokenizing data. C error: Calling read(nbytes) on source failed. Try engine='python'.

In [13]:
import os
import pandas as pd
from infrapy.utils.data_io import json_to_detection_list

def extract_det_from_csv(csv_folder, detection_file, output_folder):
    # Ensure the output folder exists
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Load the detection file
    detections = json_to_detection_list(detection_file)

    # Get a list of all CSV files in the folder
    csv_files = [f for f in os.listdir(csv_folder) if f.endswith('.csv')]

    # Process each CSV file
    for file in csv_files:
        file_path = os.path.join(csv_folder, file)

        # Read the CSV file, assuming the first column contains the timestamp
        df = pd.read_csv(file_path, index_col=0)
        df.index = pd.to_datetime(df.index)  # Convert the index to datetime

        # Iterate over each detection
        for i, det in enumerate(detections):
            # Define start and end times for slicing
            t_start = pd.to_datetime(det.peakF_UTCtime) + pd.to_timedelta(det.start, 's')
            t_end = pd.to_datetime(det.peakF_UTCtime) + pd.to_timedelta(det.end, 's')

            # Filter the DataFrame for the given detection time range
            trimmed_df = df[(df.index >= t_start) & (df.index <= t_end)]

            # Check if the trimmed DataFrame is empty and skip if true
            if trimmed_df.empty:
                print(f"No data in range for {file} detection {i}, skipping...")
                continue

            # Format times for the output filename
            t_start_str = t_start.strftime('%Y%m%d_%H%M%S')
            t_end_str = t_end.strftime('%Y%m%d_%H%M%S')

            # Save the trimmed DataFrame to a new CSV file in the output folder
            trimmed_filename = os.path.join(output_folder, f"{file.split('.')[0]}_det_{i}_{t_start_str}_to_{t_end_str}.csv")
            trimmed_df.to_csv(trimmed_filename, index=True)
            print(f"Saved trimmed data to {trimmed_filename}")

# Example usage of the function
csv_folder = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_CSV'
detection_file = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/Trimmed_Confirmed_Events.json'
output_folder = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/processed/I06AU_DETS'
extract_det_from_csv(csv_folder, detection_file, output_folder)


No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 0, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 1, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 2, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 3, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 4, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 5, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 6, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 7, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 8, skipping...
No data in range for IM.I06H_..BDF__20181024T000000Z__20181025T000000Z.csv detection 9, skipping...


In [3]:
from src.utils.converter import *

In [4]:
sac_file_parser

<function src.utils.converter.sac_file_parser(filepath)>

In [9]:
from obspy import read
import numpy as np
import csv

def calc_acoust_power_2b(trace, fac, r, rho_air, cel, aref, ref_pressure=20e-6):
    """
    Calculate acoustic power for '2b' case using an ObsPy Trace object.

    Parameters:
    - trace: ObsPy Trace object containing the waveform data in Pascals (Pa).
    - fac: Geometric spreading factor (1, 2, 4, etc.).
    - r: Distance from sensor to source in meters.
    - rho_air: Air density in kg/m^3.
    - cel: Speed of sound in air in m/s.
    - aref: Reference acoustic pressure (usually 20 microPascals).
    - ref_pressure: Reference pressure for dB conversion (default 20 microPascals).

    Returns:
    - Ea: Array of acoustic power in Watts.
    """

    # Ensure trace.data does not have zero or negative values
    trace.data = np.maximum(trace.data, 1e-10)

    # Convert amplitude data to dB
    datavec = 20 * np.log10(trace.data / ref_pressure)

    # Calculate geometric spreading factor and other constants
    omega = fac * np.pi * r**2
    int_fac = 1 / (rho_air * cel)
    
    # Convert dB to pressure and calculate acoustic power
    del_p = aref * 10 ** (datavec / 20)
    ea = omega * int_fac * del_p ** 2

    return ea

def write_to_csv(trace, ea, filename):
    """
    Write time and acoustic power to a CSV file.

    Parameters:
    - trace: ObsPy Trace object containing the waveform data.
    - ea: Array of acoustic power in Watts.
    - filename: Name of the output CSV file.
    """
    with open(filename, 'w', newline='') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(['Time', 'Acoustic Power (W)'])
        
        start_time = trace.stats.starttime
        delta = trace.stats.delta
        for i, power in enumerate(ea):
            timestamp = start_time + i * delta
            csvwriter.writerow([timestamp, power])


In [10]:
# Example usage
trace = read("/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_SAC/IM.I06H4..BDF__20190604T000000Z__20190605T000000Z.sac")[0]  # Load your waveform data

# Parameters
fac = 1       # Geometric spreading factor
r = 1000      # Distance in meters
rho_air = 1.225  # Air density in kg/m^3
cel = 343        # Speed of sound in m/s
aref = 1         # Reference acoustic pressure in microPascals

ea = calc_acoust_power_2b(trace, fac, r, rho_air, cel, aref)

# Write the results to a CSV file
output_filename = "acoustic_power_timeseries.csv"
write_to_csv(trace, ea, output_filename)
print(f"Acoustic power time series saved to {output_filename}")

Acoustic power time series saved to acoustic_power_timeseries.csv


In [3]:
import numpy as np
from obspy.core import Trace
from scipy.integrate import trapz
from obspy import read

def calc_acoust_power(trace, mode, fac, r, rho_air, cel, tau, aref, fe=None, att=0, ref_pressure=20e-6):
    """
    Calculate acoustic power for different cases using an ObsPy Trace object.

    Parameters:
    - trace: ObsPy Trace object containing the waveform data in Pascals (Pa).
    - mode: Calculation mode ('1', '2b', '2c', '2d').
    - fac: Geometric spreading factor (1, 2, 4, etc.).
    - r: Distance from sensor to source in meters.
    - rho_air: Air density in kg/m^3.
    - cel: Speed of sound in air in m/s.
    - tau: Time window (s) for integration.
    - aref: Reference acoustic pressure (usually 20 microPascals).
    - fe: Sample rate (1/sec), required for mode '1'.
    - att: Attenuation in dB, used in modes '2c' and '2d'.
    - ref_pressure: Reference pressure for dB conversion (default 20 microPascals).

    Returns:
    - Ea: Array of acoustic power in Watts.
    """
    # Read the waveform file into an ObsPy Trace object
    trace = read(file_path)[0]

    # Ensure trace.data does not have zero or negative values
    trace.data = np.maximum(trace.data, 1e-10)

    # Calculate geometric spreading factor and other constants
    omega = fac * np.pi * r**2
    int_fac = 1 / (rho_air * cel)

    if mode == '1':
        if fe is None:
            raise ValueError("Sample rate 'fe' must be provided for mode '1'")
        x = trace.data  # Data vector
        window_len = int(tau * fe)  # Window length in samples

        ea = []
        for start in range(0, len(x), window_len):
            end = min(start + window_len, len(x))
            data2 = x[start:end] ** 2
            ea.append(omega * int_fac * (1/fe) * trapz(data2))
        ea = np.array(ea)

    elif mode == '2b':
        # Convert dB to pressure and calculate acoustic power without attenuation factor
        datavec = 20 * np.log10(trace.data / ref_pressure)
        del_p = aref * 10 ** (datavec / 20)
        ea = omega * int_fac * del_p ** 2

    elif mode in ['2c', '2d']:
        # Modes '2c' and '2d' are vector-based with or without attenuation
        t = np.arange(0, len(trace.data)) / trace.stats.sampling_rate
        ti, tf = t[0], t[-1]
        begwind = np.arange(ti, tf, tau)

        ea = []
        for beg in begwind:
            end = min(beg + tau, tf)
            idx_start = int(beg * trace.stats.sampling_rate)
            idx_end = int(end * trace.stats.sampling_rate)
            
            if mode == '2c':
                xint = np.mean(20 * np.log10(trace.data[idx_start:idx_end] / ref_pressure) + att)
            else:  # mode '2d'
                xint = np.mean(20 * np.log10(trace.data[idx_start:idx_end] / ref_pressure))
            
            del_p = aref * 10 ** (xint / 20)
            ea.append(omega * int_fac * del_p ** 2)
        ea = np.array(ea)

    else:
        raise ValueError(f"Unknown mode: {mode}")

    return ea

In [10]:
# Example usage
file_path = "/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_SAC/IM.I06H4..BDF__20190604T000000Z__20190605T000000Z.sac"  # Load your waveform data
mode = '2c'  # Choose from '1', '2b', '2c', '2d'
fac = 1
r = 1158.81
rho_air = 1.225
cel = 343
tau = 1
aref = 20e-6  # Reference acoustic pressure in Pascals
fe = 1000  # Required for mode '1'
ea = calc_acoust_power(file_path, mode, fac, r, rho_air, cel, tau, aref, fe)


In [11]:
print(ea)

[6.16275912e+10 5.14343747e+10 6.31436522e+10 ... 4.39045538e+10
 3.57859517e+10 6.36960280e+10]


In [13]:
import numpy as np

def calc_vel_radiation_pat(ea, rho_air, cel, r_cond, mode='monopole'):
    """
    Calculate the vent gas exit velocity based on the acoustic power at the vent.

    Parameters:
    - ea: Acoustic power in Watts.
    - rho_air: Air density in kg/m^3.
    - cel: Speed of sound in air in m/s.
    - r_cond: Conduit radius in meters.
    - mode: 'monopole' or 'dipole' (default is 'monopole').

    Returns:
    - v_gas: Vent gas exit velocity for the selected mode.
    """

    if mode == 'monopole':
        n, m, K, f = 4, 1, 1, 4
        v_gas = ((ea * cel**m) / (K * f * rho_air * np.pi * r_cond**2))**(1/n)

    elif mode == 'dipole':
        n, m, K, f = 6, 3, 1.3e-2, 1
        v_gas = ((ea * cel**m) / (K * f * rho_air * np.pi * r_cond**2))**(1/n)

    else:
        raise ValueError("Invalid mode. Choose 'monopole' or 'dipole'.")

    return v_gas

# Example usage
rho_air = 1.225  # Air density in kg/m^3
cel = 343  # Speed of sound in air in m/s
r_cond = 2  # Conduit radius in meters

# Calculate for monopole
monopole_velocity = calc_vel_radiation_pat(ea, rho_air, cel, r_cond, mode='monopole')
print("Monopole Velocity:", monopole_velocity)



Monopole Velocity: [765.44826378 731.61973228 770.11302444 ... 703.23331374 668.1903308
 771.79174991]


In [14]:
def calculate_volumetric_flux(v_gas, R):
    """
    Calculate the volumetric flux based on gas exit velocity and vent radius.

    Parameters:
    - v_gas: Gas exit velocity (m/s).
    - R: Vent radius (m).

    Returns:
    - Q: Volumetric flux (m^3/s).
    """
    Q = np.pi * R**2 * v_gas
    return Q

v_gas = monopole_velocity
R = 10 
Q = calculate_volumetric_flux(v_gas, R)
print(f"Volumetric flux: {Q} m^3/s")

Volumetric flux: [240472.66422046 229845.11761482 241938.14200224 ... 220927.26122045
 209918.18344352 242465.52916233] m^3/s


In [16]:
def calculate_plume_height(Q):
    """
    Calculate the plume height using Mastin et al. (2009) formula.

    Parameters:
    - Q_m: Mass eruption rate in kg/s.

    Returns:
    - H_t: Plume height in meters.
    """
    H_t = 2.00 * Q**0.241
    return H_t

# Example usage
H_t = calculate_plume_height(Q)
print(f"Plume height: {H_t} meters")


Plume height: [39.61565428 39.18644796 39.67370337 ... 38.81450742 38.33928947
 39.69452842] meters


In [17]:
import obspy
import numpy as np
from infrapy.detection import data_io
from infrapy.propagation.infrasound import calc_acoust_power_2b

def process_detections_with_acoustic_power(trace_file, detection_file, fac, r, rho_air, aref, ref_pressure=20e-6):
    """
    Process detections from a JSON file and calculate acoustic power.

    Parameters:
    - trace_file: Path to the waveform file in SAC format.
    - detection_file: Path to the detection JSON file.
    - fac: Geometric spreading factor.
    - r: Distance from sensor to source in meters.
    - rho_air: Air density in kg/m^3.
    - aref: Reference acoustic pressure.
    - ref_pressure: Reference pressure for dB conversion (default 20 microPascals).
    """

    # Read the waveform data
    stream = obspy.read(trace_file)
    trace = stream[0]  # Assuming one trace in the stream

    # Read detection data
    detections = data_io.json_to_detection_list(detection_file)

    # Process each detection
    for det in detections:
        # Extract waveform for the detection window
        start_time = det.time - trace.stats.starttime
        end_time = det.endtime - trace.stats.starttime

        # Extract trace segment for this detection
        trace_segment = trace.slice(starttime=start_time, endtime=end_time)

        # Use trace velocity from detection for 'cel' parameter
        cel = det.trace_velocity

        # Calculate acoustic power
        ea = calc_acoust_power(trace_segment, fac, r, rho_air, cel, aref, ref_pressure)

        # Output or store results as needed
        # ...

    # Additional processing or output
    # ...

# Example usage
trace_file = 'path/to/waveform.sac'
detection_file = 'path/to/detections.json'
process_detections_with_acoustic_power(trace_file, detection_file, fac=1, r=1000, rho_air=1.225, aref=20e-6)


[7.6427182e+10 7.4883867e+10 7.3954345e+10 ... 6.5748353e+10 6.6005561e+10
 8.3104186e+10]


In [31]:
import csv
from obspy import UTCDateTime
import numpy as np
from scipy.integrate import trapz
from infrapy.utils.data_io import json_to_detection_list
from datetime import datetime
import pandas as pd

# Add the necessary functions (calc_acoust_power, calc_vel_radiation_pat, calculate_volumetric_flux, calculate_plume_height)

def run_infraplume(trace_file, detection_file, fac, r, rho_air, aref, output_dir, ref_pressure=20e-6):
    # Read the waveform data
    stream = obspy.read(trace_file)
    trace = stream[0]

    # Read detection data
    detections = json_to_detection_list(detection_file)

    for idx, det in enumerate(detections):
        output_csv = f"{output_dir}/detection_{idx+1}.csv"

        # Convert detection start and end times to UTCDateTime objects
        utc_time = UTCDateTime(det.peakF_UTCtime)
        start_time = utc_time + det.start
        end_time = utc_time + det.end

        with open(output_csv, 'w', newline='') as csvfile:
            csvwriter = csv.writer(csvfile)
            csvwriter.writerow(['Datetime', 'Acoustic Power (W)', 'Exit Velocity (m/s)', 'Volumetric Flux (m^3/s)', 'Plume Height (m)'])

            # Extract trace segment for this detection
            trace_segment = trace.slice(starttime=start_time, endtime=end_time)

            # Process trace segment data
            for sample in trace_segment:
                sample_time = sample.stats.starttime
                ea = calc_acoust_power(sample, fac, r, rho_air, det.trace_velocity, aref, ref_pressure)
                v_gas = calc_vel_radiation_pat(ea, rho_air, det.trace_velocity, det.radius, mode='monopole')
                q = calculate_volumetric_flux(v_gas, det.radius)
                h = calculate_plume_height(q)

                csvwriter.writerow([sample_time.isoformat(), ea, v_gas, q, h])

        print(f"Output for detection {idx+1} saved to {output_csv}")


# Example usage
trace_file = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_SAC/IM.I06H1..BDF__20181226T000000Z__20181227T000000Z.sac'
detection_file = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_FD_RESULTS/IM.I06H_2018.12.27_00.00.00-00.00.19.dets.json'
output_dir = '/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/processed/test'
r = 1158.81  # User-defined distance
run_infraplume(trace_file, detection_file, 1, r, 1.225, 20e-6, output_dir)


TypeError: int() argument must be a string, a bytes-like object or a number, not 'datetime.datetime'

In [24]:
from infrapy.utils.data_io import json_to_detection_list

detections = json_to_detection_list(detection_file)
print(detections)

In [5]:
import numpy as np
from obspy.core import Trace
from scipy.integrate import trapz
from obspy import read

def calc_acoust_power(trace, mode, fac, r, cel, tau, aref, fe=None, att=0, ref_pressure=20e-6, filter_freq=None, rho_air=1.225):
    """
    Calculate acoustic power for different cases using an ObsPy Trace object.

    Parameters:
    - trace: ObsPy Trace object containing the waveform data in Pascals (Pa).
    - mode: Calculation mode ('1', '2b', '2c', '2d').
    - fac: Geometric spreading factor (1, 2, 4, etc.).
    - r: Distance from sensor to source in meters.
    - rho_air: Air density in kg/m^3.
    - cel: Speed of sound in air in m/s.
    - tau: Time window (s) for integration.
    - aref: Reference acoustic pressure (usually 20 microPascals).
    - fe: Sample rate (1/sec), required for mode '1'.
    - att: Attenuation in dB, used in modes '2c' and '2d'.
    - ref_pressure: Reference pressure for dB conversion (default 20 microPascals).

    Returns:
    - Ea: Array of acoustic power in Watts.
    """
    # Read the waveform file into an ObsPy Trace object
    trace = read(trace)[0]
    
    # Apply a low-pass filter if the frequency is specified
    if filter_freq is not None:
        trace.filter('lowpass', freq=filter_freq, corners=2, zerophase=True)


    # Ensure trace.data does not have zero or negative values
    trace.data = np.maximum(trace.data, 1e-10)

    # Calculate geometric spreading factor and other constants
    omega = fac * np.pi * r**2
    int_fac = 1 / (rho_air * cel)

    if mode == '1':
        if fe is None:
            raise ValueError("Sample rate 'fe' must be provided for mode '1'")
        x = trace.data  # Data vector
        window_len = int(tau * fe)  # Window length in samples

        ea = []
        for start in range(0, len(x), window_len):
            end = min(start + window_len, len(x))
            data2 = x[start:end] ** 2
            ea.append(omega * int_fac * (1/fe) * trapz(data2))
        ea = np.array(ea)

    elif mode == '2b':
        # Convert dB to pressure and calculate acoustic power without attenuation factor
        datavec = 20 * np.log10(trace.data / ref_pressure)
        del_p = aref * 10 ** (datavec / 20)
        ea = omega * int_fac * del_p ** 2

    elif mode in ['2c', '2d']:
        # Modes '2c' and '2d' are vector-based with or without attenuation
        t = np.arange(0, len(trace.data)) / trace.stats.sampling_rate
        ti, tf = t[0], t[-1]
        begwind = np.arange(ti, tf, tau)

        ea = []
        for beg in begwind:
            end = min(beg + tau, tf)
            idx_start = int(beg * trace.stats.sampling_rate)
            idx_end = int(end * trace.stats.sampling_rate)
            
            if mode == '2c':
                xint = np.mean(20 * np.log10(trace.data[idx_start:idx_end] / ref_pressure) + att)
            else:  # mode '2d'
                xint = np.mean(20 * np.log10(trace.data[idx_start:idx_end] / ref_pressure))
            
            del_p = aref * 10 ** (xint / 20)
            ea.append(omega * int_fac * del_p ** 2)
        ea = np.array(ea)

    else:
        raise ValueError(f"Unknown mode: {mode}")

    return ea

In [6]:
# Example usage
file_path = "/run/media/viblab/Markov2/Haykal/AnakKrakatauEWS/data/raw/I06AU/I06AU_SAC/IM.I06H4..BDF__20190604T000000Z__20190605T000000Z.sac"  # Load your waveform data
mode = '2c'  # Choose from '1', '2b', '2c', '2d'
fac = 1
r = 1158.81
rho_air = 1.225
cel = 343
tau = 1
aref = 20e-6  # Reference acoustic pressure in Pascals
fe = 1000  # Required for mode '1'
ea = calc_acoust_power(file_path, mode, fac, r, rho_air, cel, tau, aref, fe)

print(ea)

[1.66653624e+117 2.27756877e+112 3.80365389e+120 2.62190239e+113
 2.92648304e+113 4.40512581e+112 6.09260528e+116 3.25718626e+108
 9.17870809e+115 5.28384435e+118 2.76145832e+117 1.21933040e+121
 2.21207884e+119 1.28192355e+115 7.78919356e+122 1.14059038e+118
 2.49514347e+116 5.65703268e+116 8.06183494e+116 1.15839261e+115
 2.81435085e+113 2.98245260e+114 1.05928544e+107 4.02394166e+112
 1.33656341e+107 3.95481380e+106 4.65396446e+113 5.80106694e+107
 3.93181506e+107 4.76187396e+105 3.65888859e+107 1.42154164e+103
 1.54987334e+106 1.09293246e+103 1.57807274e+105 1.09221079e+106
 1.24821633e+108 8.54865458e+104 8.87440459e+103 7.62585239e+103
 1.41017976e+100 9.60105399e+101 2.07522995e+107 6.33259345e+104
 2.29085898e+103 1.77164728e+106 4.04617119e+105 3.08606517e+103
 3.01253056e+107 7.01637605e+102 2.83391795e+104 4.97070550e+101
 1.11172377e+111 4.11643309e+106 5.55563190e+107 1.17125954e+108
 5.35531445e+104 7.56468903e+103 5.05084259e+103 3.32499003e+105
 5.09833977e+100 6.698873

In [9]:
import numpy as np

def calc_vel_radiation_pat(ea, rho_air, cel, r_cond, mode='monopole'):
    """
    Calculate the vent gas exit velocity based on the acoustic power at the vent.

    Parameters:
    - ea: Acoustic power in Watts.
    - rho_air: Air density in kg/m^3.
    - cel: Speed of sound in air in m/s.
    - r_cond: Conduit radius in meters.
    - mode: 'monopole' or 'dipole' (default is 'monopole').

    Returns:
    - v_gas: Vent gas exit velocity for the selected mode.
    """

    if mode == 'monopole':
        n, m, K, f = 4, 1, 1, 4
        v_gas = ((ea * cel**m) / (K * f * rho_air * np.pi * r_cond**2))**(1/n)

    elif mode == 'dipole':
        n, m, K, f = 6, 3, 1.3e-2, 1
        v_gas = ((ea * cel**m) / (K * f * rho_air * np.pi * r_cond**2))**(1/n)

    else:
        raise ValueError("Invalid mode. Choose 'monopole' or 'dipole'.")

    return v_gas

# Example usage
rho_air = 1.225  # Air density in kg/m^3
cel = 343  # Speed of sound in air in m/s
r_cond = 2  # Conduit radius in meters

# Calculate for monopole
monopole_velocity = calc_vel_radiation_pat(ea, rho_air, cel, r_cond, mode='monopole')
print("Monopole Velocity:", monopole_velocity)



Monopole Velocity: [3.10402874e+29 1.88729556e+28 2.14546924e+30 3.47637144e+28
 3.57321005e+28 2.22567436e+28 2.41364172e+29 2.06387168e+27
 1.50372158e+29 7.36562404e+29 3.52173495e+29 2.87079641e+30
 1.05359135e+30 9.19258333e+28 8.11605849e+30 5.02058668e+29
 1.93083839e+29 2.36929543e+29 2.58869282e+29 8.96264074e+28
 3.53847885e+28 6.38433154e+28 8.76446266e+26 2.17588011e+28
 9.28901011e+26 6.85099348e+26 4.01261793e+28 1.34075373e+27
 1.21652297e+27 4.03567810e+26 1.19483886e+27 9.43326295e+25
 5.42058421e+26 8.83324702e+25 3.06199021e+26 4.96647964e+26
 1.62384476e+27 2.62691782e+26 1.49110027e+26 1.43563535e+26
 1.67413572e+25 4.80896672e+25 1.03690412e+27 2.43706687e+26
 1.06284916e+26 5.60488052e+26 3.87465561e+26 1.14504701e+26
 1.13816417e+27 7.90679098e+25 1.99328254e+26 4.07921459e+25
 8.87097319e+27 6.91993968e+26 1.32634166e+27 1.59821547e+27
 2.33705153e+26 1.43274801e+26 1.29512892e+26 3.68909323e+26
 2.30849659e+25 7.81578290e+25 5.45280860e+25 1.00283040e+26
 4.04

In [10]:
def calculate_volumetric_flux(v_gas, R):
    """
    Calculate the volumetric flux based on gas exit velocity and vent radius.

    Parameters:
    - v_gas: Gas exit velocity (m/s).
    - R: Vent radius (m).

    Returns:
    - Q: Volumetric flux (m^3/s).
    """
    Q = np.pi * R**2 * v_gas
    return Q

v_gas = monopole_velocity
R = 10 
Q = calculate_volumetric_flux(v_gas, R)
print(f"Volumetric flux: {Q} m^3/s")

Volumetric flux: [9.75159390e+31 5.92911388e+30 6.74019040e+32 1.09213430e+31
 1.12255704e+31 6.99216222e+30 7.58267911e+31 6.48384412e+29
 4.72408068e+31 2.31397904e+32 1.10638566e+32 9.01887291e+32
 3.30995483e+32 2.88793522e+31 2.54973497e+33 1.57726382e+32
 6.06590770e+31 7.44336110e+31 8.13261835e+31 2.81569663e+31
 1.11164591e+31 2.00569691e+31 2.75343715e+29 6.83572898e+30
 2.91822859e+29 2.15230308e+29 1.26060110e+31 4.21210206e+29
 3.82181963e+29 1.26784567e+29 3.75369700e+29 2.96354696e+28
 1.70292675e+29 2.77504639e+28 9.61952596e+28 1.56026559e+29
 5.10145878e+29 8.25270572e+28 4.68442967e+28 4.51018146e+28
 5.25945249e+27 1.51078145e+28 3.25753037e+29 7.65627137e+28
 3.33903911e+28 1.76082515e+29 1.21725896e+29 3.59727128e+28
 3.57564819e+29 2.48399165e+28 6.26208177e+28 1.28152306e+28
 2.78689842e+30 2.17396317e+29 4.16682520e+29 5.02094197e+29
 7.34206391e+28 4.50111062e+28 4.06876751e+28 1.15896282e+29
 7.25235594e+27 2.45540061e+28 1.71305034e+28 3.15048463e+28
 1.2707

In [11]:
def calculate_plume_height(Q):
    """
    Calculate the plume height using Mastin et al. (2009) formula.

    Parameters:
    - Q_m: Mass eruption rate in kg/s.

    Returns:
    - H_t: Plume height in meters.
    """
    H_t = 2.00 * Q**0.241
    return H_t

# Example usage
H_t = calculate_plume_height(Q)
print(f"Plume height: {H_t} meters")


Plume height: [1.02422935e+08 5.21579526e+07 1.63207453e+08 6.04302684e+07
 6.08317380e+07 5.42726923e+07 9.63978307e+07 3.05971971e+07
 8.60083204e+07 1.26136453e+08 1.05587248e+08 1.75074015e+08
 1.37501398e+08 7.63891312e+07 2.24903027e+08 1.15007177e+08
 9.13498593e+07 9.59679783e+07 9.80382432e+07 7.59241936e+07
 6.06887114e+07 6.99642099e+07 2.48908605e+07 5.39775466e+07
 2.52419992e+07 2.34563116e+07 6.25560355e+07 2.75761877e+07
 2.69374890e+07 2.06475723e+07 2.68209815e+07 1.45457675e+07
 2.21691083e+07 1.43172011e+07 1.93183500e+07 2.17065519e+07
 2.88791457e+07 1.86178582e+07 1.62427016e+07 1.60949916e+07
 9.58907388e+06 1.23656683e+07 2.59200669e+07 1.82842929e+07
 1.49700337e+07 2.23484603e+07 2.04459500e+07 1.52412131e+07
 2.65087041e+07 1.39399488e+07 1.74196414e+07 1.18848051e+07
 4.34814672e+07 2.35129853e+07 2.75044566e+07 2.87686332e+07
 1.81005667e+07 1.60871844e+07 1.57003939e+07 2.02055532e+07
 1.03610904e+07 1.39011101e+07 1.27458439e+07 1.47617872e+07
 2.0658939